In [1]:
# Imports
import pandas as pd
import numpy as np
# from skmultiflow.drift_detection.adwin import ADWIN
from hyppo.ksample import KSample

import os

import time

In [11]:
# used as input to drift_detection methods
def xnor(x1, x2):
    '''
    '''
    return ~np.logical_xor(x1, x2)

In [2]:
idx=pd.IndexSlice

In [4]:
data_dir="E:\Data\HIDENIC_EXTRACT_OUTPUT_DIR\POP_SIZE_0\ITEMID_REP\hospital-style_trainHospitals_UPMCPUH_raw_Simple_seed_0_target=mort_icu.h5"

site_info = pd.read_pickle("E:/Data/HIDENIC_EXTRACT_OUTPUT_DIR/POP_SIZE_0/ITEMID_REP/site_info.pkl")

subject_info = pd.read_hdf("E:/Data/HIDENIC_EXTRACT_OUTPUT_DIR/POP_SIZE_0/ITEMID_REP/filtered_data.h5", "label_df")

subject_info=subject_info.join(site_info.set_index(['subject_id', 'hadm_id'])[['hospital', 'icu_category']],
       on=['subject_id', 'hadm_id'])

In [ ]:
hospitals = set(site_info["hospital"].unique()) - set(["UPMCPUH"])

In [3]:
X1 = pd.read_hdf(data_dir, key="X_test_UPMCPUH").drop('time', axis=1, level=2).values

In [210]:
hospitals

{'UPMCBED',
 'UPMCEAS',
 'UPMCHAM',
 'UPMCHZN',
 'UPMCMCK',
 'UPMCMER',
 'UPMCMWH',
 'UPMCNOR',
 'UPMCPAS',
 'UPMCSHY',
 'UPMCSMH'}

In [59]:
for hosp in hospitals:
    X2 = pd.read_hdf(data_dir, key="X_test_" + hosp).drop('time', axis=1, level=2).values
    stat, pvalue = KSample("Dcorr").test(X1, X2)
    print('{}: stat={:0.2f}, pval={:0.3f}'.format(hosp, stat, pvalue))
    

UPMCMWH: stat=0.21, pval=0.000
UPMCMCK: stat=0.04, pval=0.000
UPMCPAS: stat=0.32, pval=0.000
UPMCMER: stat=0.30, pval=0.000
UPMCHAM: stat=0.51, pval=0.000
UPMCHZN: stat=0.52, pval=0.000
UPMCBED: stat=0.45, pval=0.000
UPMCSMH: stat=0.47, pval=0.000
UPMCNOR: stat=0.41, pval=0.000
UPMCEAS: stat=0.46, pval=0.000
UPMCSHY: stat=0.26, pval=0.000


In [10]:
data_dir="E:/Data/HIDENIC_EXTRACT_OUTPUT_DIR/POP_SIZE_0/ITEMID_REP/"
data_files=[f for f in os.listdir(data_dir) if 'hospital-overtime-style' in f]

In [ ]:
for target in targets:
    for rep in reps:
        for f in data_files:
            if (target in f) and (rep in f):
                print(target, rep)
                X1=pd.read_hdf(os.path.join(data_dir, f), key='X_train_UPMCPUH')
                df.loc[:, idx[target, :, rep, 'base_rows']] = X1.shape[0]
                df.loc[:, idx[target, :, rep, 'base_cols']] = X1.shape[1]

                for hosp in hospitals:
                    for year in year_range:
                        for month in month_intervals:
                            if ~df.loc[(hosp, year, month), idx[target,:,rep, main_measures]].isna().all():
                                key="X_test_"+hosp+"_"+str(year)+"_"+"-".join([str(i) for i in [month-1, month]])
                                X2=pd.read_hdf(os.path.join(data_dir, f), key)
                                df.loc[(hosp, year, month), idx[target, :, rep, 'data_rows']] = X2.shape[0]
                                df.loc[(hosp, year, month), idx[target, :, rep, 'data_cols']] = X2.shape[1]
                                for indep_test in ["Dcorr"]:
                                    print('indep_test:', indep_test)
                                    t0=time.time()
                                    stat, pvalue = KSample(indep_test).test(X1.values, X2.values)
                                    t1=time.time()
                                    print("runtime=", str((t1-t0)/60), "seconds")
                                    print(hosp, year, month, indep_test, np.round(stat,2), np.round(pvalue,3))
                                    df.loc[(hosp, year, month), idx[target,:,rep, indep_test]] = pvalue

mort_icu raw
indep_test: Dcorr
runtime= 0.2233623425165812 seconds
UPMCEAS 2012 8 Dcorr 0.0 0.0
indep_test: Dcorr
runtime= 0.22421348094940186 seconds
UPMCEAS 2012 10 Dcorr 0.0 0.0
indep_test: Dcorr
runtime= 0.2303679307301839 seconds
UPMCEAS 2013 2 Dcorr 0.0 0.0
indep_test: Dcorr
runtime= 0.23010108470916749 seconds
UPMCEAS 2013 4 Dcorr 0.0 0.0
indep_test: Dcorr
runtime= 0.23210252523422242 seconds
UPMCEAS 2013 10 Dcorr 0.01 0.0
indep_test: Dcorr
runtime= 0.23363700707753499 seconds
UPMCEAS 2013 12 Dcorr 0.0 0.0
indep_test: Dcorr
runtime= 0.22664892673492432 seconds
UPMCEAS 2014 2 Dcorr 0.01 0.0
indep_test: Dcorr
runtime= 0.2212116837501526 seconds
UPMCEAS 2014 4 Dcorr 0.0 0.0
indep_test: Dcorr
runtime= 0.2205608050028483 seconds
UPMCEAS 2014 6 Dcorr 0.01 0.0
indep_test: Dcorr
runtime= 0.2293004790941874 seconds
UPMCEAS 2014 8 Dcorr 0.0 0.0
indep_test: Dcorr
runtime= 0.2258484443028768 seconds
UPMCEAS 2014 10 Dcorr 0.01 0.0
indep_test: Dcorr
runtime= 0.2316856066385905 seconds
UPMCEAS

runtime= 0.2336859146753947 seconds
UPMCMWH 2014 6 Dcorr 0.0 0.006
indep_test: Dcorr
runtime= 0.24417643149693807 seconds
UPMCPAS 2011 2 Dcorr 0.01 0.0
indep_test: Dcorr
runtime= 0.2502808451652527 seconds
UPMCPAS 2011 4 Dcorr 0.02 0.0
indep_test: Dcorr
runtime= 0.23468627532323202 seconds
UPMCPAS 2011 6 Dcorr 0.02 0.0
indep_test: Dcorr
runtime= 0.23567029237747192 seconds
UPMCPAS 2011 8 Dcorr 0.01 0.0
indep_test: Dcorr
runtime= 0.23273483514785767 seconds
UPMCPAS 2011 10 Dcorr 0.01 0.0
indep_test: Dcorr
runtime= 0.23618777990341186 seconds
UPMCPAS 2011 12 Dcorr 0.02 0.0
indep_test: Dcorr
runtime= 0.23018300135930378 seconds
UPMCPAS 2012 2 Dcorr 0.01 0.0
indep_test: Dcorr
runtime= 0.24192482630411785 seconds
UPMCPAS 2012 4 Dcorr 0.02 0.0
indep_test: Dcorr
runtime= 0.24357601006825766 seconds
UPMCPAS 2012 6 Dcorr 0.01 0.0
indep_test: Dcorr
runtime= 0.23992336591084798 seconds
UPMCPAS 2012 8 Dcorr 0.03 0.0
indep_test: Dcorr
runtime= 0.23592050472895304 seconds
UPMCPAS 2012 10 Dcorr 0.02 

In [5]:
df_results = pd.read_pickle("../../../output/HIDENIC_overtime_analysis/hospital_overtime/results_df.pkl")

In [6]:
data_dir="E:/Data/HIDENIC_EXTRACT_OUTPUT_DIR/POP_SIZE_0/ITEMID_REP/"
data_files=[f for f in os.listdir(data_dir) if ('hospital-overtime-style' in f) and ('data_flat' in f)]

In [7]:
data_files

['hospital-overtime-style_UPMCPUH_2008-2009-2010_data_flat_pca_Simple_seed_0_target=los_3.h5',
 'hospital-overtime-style_UPMCPUH_2008-2009-2010_data_flat_pca_Simple_seed_0_target=mort_icu.h5',
 'hospital-overtime-style_UPMCPUH_2008-2009-2010_data_flat_raw_Simple_seed_0_target=los_3.h5',
 'hospital-overtime-style_UPMCPUH_2008-2009-2010_data_flat_raw_Simple_seed_0_target=mort_icu.h5']

In [14]:
out_dir="../../../output/HIDENIC_overtime_analysis/hospital_overtime/"

targets = ['mort_icu', 'los_3']
reps = ['pca', 'raw']
independent_tests = ["CCA", "RV", "MGC", "HHG"]
main_measures = ['AUC', 'APR', 'Acc', 'F1', 'ECE', 'MCE', 'O_E']


hospitals = sorted(site_info["hospital"].unique().tolist())
year_range = np.arange(2011, 2015)
month_step = 2
month_intervals = np.arange(month_step, 13, month_step)

# columns=[]
# for target in targets:
#         for representation in reps:
#             for indep_test in ['base_rows', 'base_cols', 'data_rows', 'data_cols'] + independent_tests:
#                 columns.append((target, representation, indep_test))

# ind=[(hosp, yr, mnth) for hosp in hospitals for yr in year_range for mnth in month_intervals]
# ind=pd.MultiIndex.from_tuples(ind, names=('hospital', 'year', 'month'))
# cols=pd.MultiIndex.from_tuples(columns, names=('target', 'representation', 'indep_test'))
# indep_test_df=pd.DataFrame(index=ind, columns=cols)

In [11]:
indep_test_df = pd.read_pickle(os.path.join(out_dir, "indep_tests.pkl"))

In [ ]:
for indep_test in independent_tests:
    print('indep_test:', indep_test)
    if indep_test=='Dcorr':
        ## I computed this before, skip
        continue
    for target in targets:
        for rep in reps:
            for f in data_files:
                if (target in f) and ("data_flat_"+rep in f):
                    print(target, rep)
                    X1=pd.read_hdf(os.path.join(data_dir, f), key='X_train_UPMCPUH')
                    print('X1_shape:', X1.shape)

                    indep_test_df.loc[:, idx[target, rep, 'base_rows']] = X1.shape[0]
                    indep_test_df.loc[:, idx[target, rep, 'base_cols']] = X1.shape[1]

                    for hosp in hospitals:
                        for year in year_range:
                            for month in month_intervals:
                                if ~df_results.loc[(hosp, year, month), idx[target,:,rep, main_measures]].isna().all():
                                    ## if any non-null measures is available for (hosp, year, month) index
                                    key="X_test_"+hosp+"_"+str(year)+"_"+"-".join([str(i) for i in [month-1, month]])
                                    X2=pd.read_hdf(os.path.join(data_dir, f), key)
                                    print('X2_shape:', X2.shape)
                                    indep_test_df.loc[(hosp, year, month), idx[target, rep, 'data_rows']] = X2.shape[0]
                                    indep_test_df.loc[(hosp, year, month), idx[target, rep, 'data_cols']] = X2.shape[1]
                                    
                                    t0=time.time()
                                    np.random.seed(0)
                                    stat, pvalue = KSample(indep_test).test(X1.values, X2.values, workers=6, auto=True)
                                    t1=time.time()
                                    print("runtime=", str((t1-t0)), "seconds")
                                    print(hosp, year, month, indep_test, np.round(stat,3), np.round(pvalue,3))
                                    
                                    indep_test_df.loc[(hosp, year, month), idx[target, rep, indep_test]] = pvalue
                                    indep_test_df.to_csv(os.path.join(out_dir, "indep_tests.csv"))
                                    indep_test_df.to_pickle(os.path.join(out_dir, "indep_tests.pkl"))
                                    print('#'*60)

indep_test: CCA
mort_icu pca
X1_shape: (7172, 1775)
X2_shape: (104, 1775)
runtime= 196.71182084083557 seconds
UPMCEAS 2012 8 CCA 0.003 0.001
############################################################
X2_shape: (64, 1775)
runtime= 198.3753800392151 seconds
UPMCEAS 2012 10 CCA 0.001 0.003
############################################################
X2_shape: (59, 1775)
runtime= 203.97365498542786 seconds
UPMCEAS 2013 2 CCA 0.004 0.001
############################################################
X2_shape: (50, 1775)
runtime= 197.26373529434204 seconds
UPMCEAS 2013 4 CCA 0.001 0.004
############################################################
X2_shape: (64, 1775)
runtime= 197.06259679794312 seconds
UPMCEAS 2013 10 CCA 0.002 0.001
############################################################
X2_shape: (52, 1775)
runtime= 196.78937911987305 seconds
UPMCEAS 2013 12 CCA 0.002 0.001
############################################################
X2_shape: (55, 1775)
runtime= 196.7465958595276 sec

runtime= 205.16294121742249 seconds
UPMCMCK 2011 12 CCA 0.008 0.001
############################################################
X2_shape: (108, 1775)
runtime= 207.92584824562073 seconds
UPMCMCK 2012 2 CCA 0.009 0.001
############################################################
X2_shape: (119, 1775)
runtime= 236.9067840576172 seconds
UPMCMCK 2012 4 CCA 0.003 0.001
############################################################
X2_shape: (120, 1775)
runtime= 237.0533049106598 seconds
UPMCMCK 2012 6 CCA 0.004 0.001
############################################################
X2_shape: (107, 1775)
runtime= 240.19657564163208 seconds
UPMCMCK 2012 8 CCA 0.005 0.001
############################################################
X2_shape: (93, 1775)
runtime= 244.44064283370972 seconds
UPMCMCK 2012 10 CCA 0.004 0.001
############################################################
X2_shape: (102, 1775)
runtime= 246.66624927520752 seconds
UPMCMCK 2012 12 CCA 0.01 0.012
##################################

runtime= 231.69492530822754 seconds
UPMCPAS 2013 2 CCA 0.006 0.001
############################################################
X2_shape: (179, 1775)
runtime= 230.91035223007202 seconds
UPMCPAS 2013 4 CCA 0.006 0.001
############################################################
X2_shape: (182, 1775)
runtime= 229.22112274169922 seconds
UPMCPAS 2013 6 CCA 0.006 0.001
############################################################
X2_shape: (167, 1775)
runtime= 227.90216040611267 seconds
UPMCPAS 2013 8 CCA 0.005 0.001
############################################################
X2_shape: (152, 1775)
runtime= 229.95465564727783 seconds
UPMCPAS 2013 10 CCA 0.008 0.001
############################################################
X2_shape: (132, 1775)
runtime= 235.53729701042175 seconds
UPMCPAS 2013 12 CCA 0.008 0.001
############################################################
X2_shape: (175, 1775)
runtime= 228.83793544769287 seconds
UPMCPAS 2014 2 CCA 0.009 0.001
###############################

runtime= 200.44229412078857 seconds
UPMCSHY 2014 4 CCA 0.005 0.001
############################################################
X2_shape: (192, 1775)
runtime= 200.14432168006897 seconds
UPMCSHY 2014 6 CCA 0.006 0.001
############################################################
X2_shape: (213, 1775)
runtime= 200.82424354553223 seconds
UPMCSHY 2014 8 CCA 0.006 0.001
############################################################
X2_shape: (226, 1775)
runtime= 201.1595721244812 seconds
UPMCSHY 2014 10 CCA 0.005 0.001
############################################################
X2_shape: (156, 1775)
runtime= 200.35600399971008 seconds
UPMCSHY 2014 12 CCA 0.005 0.001
############################################################
X2_shape: (69, 1775)
runtime= 197.1724922657013 seconds
UPMCSMH 2011 2 CCA 0.005 0.001
############################################################
X2_shape: (74, 1775)
runtime= 197.28970956802368 seconds
UPMCSMH 2011 6 CCA 0.001 0.002
###################################

runtime= 2804.0804936885834 seconds
UPMCHZN 2012 2 CCA 0.013 0.001
############################################################
X2_shape: (87, 7657)
runtime= 2809.5104944705963 seconds
UPMCHZN 2012 4 CCA 0.009 0.001
############################################################
X2_shape: (84, 7657)
runtime= 2811.253610610962 seconds
UPMCHZN 2012 6 CCA 0.01 0.001
############################################################
X2_shape: (83, 7657)
runtime= 2802.55815076828 seconds
UPMCHZN 2012 8 CCA 0.01 0.001
############################################################
X2_shape: (89, 7657)
runtime= 2799.1811623573303 seconds
UPMCHZN 2012 10 CCA 0.01 0.001
############################################################
X2_shape: (79, 7657)
runtime= 2798.140387773514 seconds
UPMCHZN 2012 12 CCA 0.009 0.001
############################################################
X2_shape: (88, 7657)
runtime= 2797.6608850955963 seconds
UPMCHZN 2013 2 CCA 0.009 0.001
############################################

runtime= 2909.4303045272827 seconds
UPMCMER 2013 10 CCA 0.022 0.001
############################################################
X2_shape: (165, 7657)
runtime= 2853.3872604370117 seconds
UPMCMER 2013 12 CCA 0.025 0.001
############################################################
X2_shape: (137, 7657)
runtime= 2852.6371080875397 seconds
UPMCMER 2014 2 CCA 0.024 0.001
############################################################
X2_shape: (186, 7657)
runtime= 2848.732966899872 seconds
UPMCMER 2014 4 CCA 0.03 0.001
############################################################
X2_shape: (152, 7657)
runtime= 2837.0999369621277 seconds
UPMCMER 2014 6 CCA 0.019 0.001
############################################################
X2_shape: (179, 7657)
runtime= 2863.2925295829773 seconds
UPMCMER 2014 8 CCA 0.019 0.001
############################################################
X2_shape: (187, 7657)
runtime= 2853.9306824207306 seconds
UPMCMER 2014 10 CCA 0.021 0.001
################################

runtime= 2930.9723563194275 seconds
UPMCPUH 2014 6 CCA 0.006 0.001
############################################################
X2_shape: (451, 7657)
runtime= 2965.775199174881 seconds
UPMCPUH 2014 8 CCA 0.002 0.001
############################################################
X2_shape: (453, 7657)
runtime= 2945.893723011017 seconds
UPMCPUH 2014 10 CCA 0.008 0.001
############################################################
X2_shape: (314, 7657)
runtime= 2893.5305466651917 seconds
UPMCPUH 2014 12 CCA 0.009 0.001
############################################################
X2_shape: (291, 7657)
runtime= 2889.697262763977 seconds
UPMCSHY 2011 2 CCA 0.017 0.001
############################################################
X2_shape: (309, 7657)
runtime= 2975.668226003647 seconds
UPMCSHY 2011 4 CCA 0.019 0.001
############################################################
X2_shape: (297, 7657)
runtime= 2885.613635778427 seconds
UPMCSHY 2011 6 CCA 0.023 0.001
####################################

# analyse data after feature-selection

In [3]:
data_dir="E:/Data/HIDENIC_EXTRACT_OUTPUT_DIR/POP_SIZE_0/ITEMID_REP/preprocessed_data/"
data_files=[f for f in os.listdir(data_dir) if ('hospital-overtime-style' in f) and ('data_flat' in f)]

data_files

['hospital-overtime-style_UPMCPUH_2008-2009-2010_data_flat_pca_Simple_seed_0_target=los_3.h5',
 'hospital-overtime-style_UPMCPUH_2008-2009-2010_data_flat_pca_Simple_seed_0_target=mort_icu.h5',
 'hospital-overtime-style_UPMCPUH_2008-2009-2010_data_flat_raw_Simple_seed_0_target=los_3.h5',
 'hospital-overtime-style_UPMCPUH_2008-2009-2010_data_flat_raw_Simple_seed_0_target=mort_icu.h5']

In [5]:
out_dir="../../../output/HIDENIC_overtime_analysis/hospital_overtime_fselect/"

df_results = pd.read_pickle(os.path.join(out_dir, "results_df.pkl"))
site_info = pd.read_pickle("E:/Data/HIDENIC_EXTRACT_OUTPUT_DIR/POP_SIZE_0/ITEMID_REP/site_info.pkl")

models=['rf','lr','nb','rbf-svm']
targets = ['mort_icu', 'los_3']
reps = ['pca', 'raw']
independent_tests = ["CCA", "Dcorr", "RV", "Hsic", "HHG", "MGC"]
main_measures = ['AUC', 'APR', 'ECE']


hospitals = sorted(site_info["hospital"].unique().tolist())
year_range = np.arange(2011, 2015)
month_step = 2
month_intervals = np.arange(month_step, 13, month_step)

In [7]:
columns=[]
for target in targets:
        for representation in reps:
            for modeltype in models:
                for indep_test in ['base_rows', 'base_cols', 'data_rows', 'data_cols'] + independent_tests:
                    columns.append((target, representation, modeltype, indep_test))

ind=[(hosp, yr, mnth) for hosp in hospitals for yr in year_range for mnth in month_intervals]
ind=pd.MultiIndex.from_tuples(ind, names=('hospital', 'year', 'month'))
cols=pd.MultiIndex.from_tuples(columns, names=('target', 'representation', 'model', 'indep_test'))
indep_test_df=pd.DataFrame(index=ind, columns=cols)

In [ ]:
for indep_test in independent_tests:
    print('indep_test:', indep_test)
    for target in targets:
        for rep in reps:
            for f in data_files:
                if (target in f) and ("data_flat_"+rep in f):
                    print(target, rep)
                    for modeltype in models:
                        print(modeltype)
                        data_key= "X_test_UPMCPUH_2011_1-2_"+modeltype.upper()
                        try:
                            X1=pd.read_hdf(os.path.join(data_dir, f), key=data_key)
                        except KeyError as ke:
                            data_key= "X_test_UPMCPUH_2011_1-2_"+modeltype
                            X1=pd.read_hdf(os.path.join(data_dir, f), key=data_key)
                            
                        print('X1_shape:', X1.shape)

                        indep_test_df.loc[:, idx[target, rep, modeltype, 'base_rows']] = X1.shape[0]
                        indep_test_df.loc[:, idx[target, rep, modeltype, 'base_cols']] = X1.shape[1]

                        for hosp in hospitals:
                            for year in year_range:
                                for month in month_intervals:
                                    if ~df_results.loc[(hosp, year, month), idx[target,:,rep, main_measures]].isna().all():
                                        ## if any non-null measures is available for (hosp, year, month) index
                                        print(indep_test, target, rep, modeltype, hosp, year, month)
                                        data_key="X_test_"+hosp+"_"+str(year)+"_"+"-".join([str(i) for i in [month-1, month]])+"_"+modeltype.upper()
                                        try:
                                            X2=pd.read_hdf(os.path.join(data_dir, f), key=data_key)
                                        except KeyError as ke:
                                            data_key="X_test_"+hosp+"_"+str(year)+"_"+"-".join([str(i) for i in [month-1, month]])+"_"+modeltype
                                            X2=pd.read_hdf(os.path.join(data_dir, f), key=data_key)
                                        print('X2_shape:', X2.shape)
                                        indep_test_df.loc[(hosp, year, month), idx[target, rep, modeltype, 'data_rows']] = X2.shape[0]
                                        indep_test_df.loc[(hosp, year, month), idx[target, rep, modeltype, 'data_cols']] = X2.shape[1]

                                        t0=time.time()
                                        np.random.seed(0)
                                        stat, pvalue = KSample(indep_test).test(X1.values, X2.values, workers=6, auto=True)
                                        t1=time.time()
                                        print("runtime=", str((t1-t0)), "seconds")
                                        print("stat, pval= {:0.3f}, {:0.3f}".format(stat, pvalue))

                                        indep_test_df.loc[(hosp, year, month), idx[target, rep, modeltype, indep_test]] = pvalue
                                        indep_test_df.to_csv(os.path.join(out_dir, "indep_tests.csv"))
                                        indep_test_df.to_pickle(os.path.join(out_dir, "indep_tests.pkl"))
                                        print('*'*30)

indep_test: CCA
mort_icu pca
rf
X1_shape: (540, 1000)
CCA mort_icu pca rf UPMCEAS 2012 8
X2_shape: (104, 1000)
runtime= 13.467366456985474 seconds
stat, pval= 0.025, 0.001
******************************
CCA mort_icu pca rf UPMCEAS 2012 10
X2_shape: (64, 1000)
runtime= 10.517669439315796 seconds
stat, pval= 0.009, 0.025
******************************
CCA mort_icu pca rf UPMCEAS 2013 2
X2_shape: (59, 1000)
runtime= 10.010329008102417 seconds
stat, pval= 0.036, 0.001
******************************
CCA mort_icu pca rf UPMCEAS 2013 4
X2_shape: (50, 1000)
runtime= 9.838172674179077 seconds
stat, pval= 0.009, 0.029
******************************
CCA mort_icu pca rf UPMCEAS 2013 10
X2_shape: (64, 1000)
runtime= 9.975272178649902 seconds
stat, pval= 0.018, 0.001
******************************
CCA mort_icu pca rf UPMCEAS 2013 12
X2_shape: (52, 1000)
runtime= 10.048303365707397 seconds
stat, pval= 0.015, 0.001
******************************
CCA mort_icu pca rf UPMCEAS 2014 2
X2_shape: (55, 1000)


runtime= 10.40658688545227 seconds
stat, pval= 0.017, 0.001
******************************
CCA mort_icu pca rf UPMCMCK 2012 2
X2_shape: (108, 1000)
runtime= 10.25939130783081 seconds
stat, pval= 0.011, 0.001
******************************
CCA mort_icu pca rf UPMCMCK 2012 4
X2_shape: (119, 1000)
runtime= 10.403559684753418 seconds
stat, pval= 0.015, 0.001
******************************
CCA mort_icu pca rf UPMCMCK 2012 6
X2_shape: (120, 1000)
runtime= 10.515440940856934 seconds
stat, pval= 0.028, 0.001
******************************
CCA mort_icu pca rf UPMCMCK 2012 8
X2_shape: (107, 1000)
runtime= 10.363525390625 seconds
stat, pval= 0.014, 0.003
******************************
CCA mort_icu pca rf UPMCMCK 2012 10
X2_shape: (93, 1000)
runtime= 10.181451320648193 seconds
stat, pval= 0.023, 0.001
******************************
CCA mort_icu pca rf UPMCMCK 2012 12
X2_shape: (102, 1000)
runtime= 10.235007762908936 seconds
stat, pval= 0.008, 0.156
******************************
CCA mort_icu pca r

runtime= 11.121111154556274 seconds
stat, pval= 0.039, 0.001
******************************
CCA mort_icu pca rf UPMCPAS 2013 6
X2_shape: (182, 1000)
runtime= 11.26142168045044 seconds
stat, pval= 0.035, 0.001
******************************
CCA mort_icu pca rf UPMCPAS 2013 8
X2_shape: (167, 1000)
runtime= 11.106910467147827 seconds
stat, pval= 0.028, 0.001
******************************
CCA mort_icu pca rf UPMCPAS 2013 10
X2_shape: (152, 1000)
runtime= 10.964365482330322 seconds
stat, pval= 0.057, 0.001
******************************
CCA mort_icu pca rf UPMCPAS 2013 12
X2_shape: (132, 1000)
runtime= 10.392578125 seconds
stat, pval= 0.061, 0.001
******************************
CCA mort_icu pca rf UPMCPAS 2014 2
X2_shape: (175, 1000)
runtime= 10.850910663604736 seconds
stat, pval= 0.057, 0.001
******************************
CCA mort_icu pca rf UPMCPAS 2014 4
X2_shape: (201, 1000)
runtime= 11.08708381652832 seconds
stat, pval= 0.042, 0.001
******************************
CCA mort_icu pca rf 

runtime= 11.596150636672974 seconds
stat, pval= 0.036, 0.001
******************************
CCA mort_icu pca rf UPMCSHY 2014 8
X2_shape: (213, 1000)
runtime= 11.427122354507446 seconds
stat, pval= 0.032, 0.001
******************************
CCA mort_icu pca rf UPMCSHY 2014 10
X2_shape: (226, 1000)
runtime= 11.960418701171875 seconds
stat, pval= 0.019, 0.001
******************************
CCA mort_icu pca rf UPMCSHY 2014 12
X2_shape: (156, 1000)
runtime= 11.36136531829834 seconds
stat, pval= 0.032, 0.001
******************************
CCA mort_icu pca rf UPMCSMH 2011 2
X2_shape: (69, 1000)
runtime= 10.303513288497925 seconds
stat, pval= 0.046, 0.001
******************************
CCA mort_icu pca rf UPMCSMH 2011 6
X2_shape: (74, 1000)
runtime= 10.10130262374878 seconds
stat, pval= 0.010, 0.019
******************************
CCA mort_icu pca rf UPMCSMH 2011 8
X2_shape: (71, 1000)
runtime= 10.357039451599121 seconds
stat, pval= 0.019, 0.001
******************************
CCA mort_icu pca 

runtime= 1.0327520370483398 seconds
stat, pval= 0.031, 0.001
******************************
CCA mort_icu pca lr UPMCHZN 2012 8
X2_shape: (83, 200)
runtime= 0.9977281093597412 seconds
stat, pval= 0.033, 0.001
******************************
CCA mort_icu pca lr UPMCHZN 2012 10
X2_shape: (89, 200)
runtime= 1.026749849319458 seconds
stat, pval= 0.045, 0.001
******************************
CCA mort_icu pca lr UPMCHZN 2012 12
X2_shape: (79, 200)
runtime= 1.0037312507629395 seconds
stat, pval= 0.042, 0.001
******************************
CCA mort_icu pca lr UPMCHZN 2013 2
X2_shape: (88, 200)
runtime= 1.064774751663208 seconds
stat, pval= 0.047, 0.001
******************************
CCA mort_icu pca lr UPMCHZN 2013 4
X2_shape: (73, 200)
runtime= 0.9937252998352051 seconds
stat, pval= 0.049, 0.001
******************************
CCA mort_icu pca lr UPMCHZN 2013 6
X2_shape: (82, 200)
runtime= 1.0667767524719238 seconds
stat, pval= 0.039, 0.001
******************************
CCA mort_icu pca lr UPMCHZ

...

runtime= 1020.8242664337158 seconds
stat, pval= 2710762.461, 0.001
******************************
HHG mort_icu pca rf UPMCPAS 2012 10
X2_shape: (187, 1000)
runtime= 1081.1532499790192 seconds
stat, pval= 2957913.441, 0.001
******************************
HHG mort_icu pca rf UPMCPAS 2012 12
X2_shape: (173, 1000)
runtime= 1003.3195040225983 seconds
stat, pval= 2160349.535, 0.001
******************************
HHG mort_icu pca rf UPMCPAS 2013 2
X2_shape: (170, 1000)
runtime= 1079.0827395915985 seconds
stat, pval= 2295718.786, 0.001
******************************
HHG mort_icu pca rf UPMCPAS 2013 4
X2_shape: (179, 1000)
runtime= 1180.4686846733093 seconds
stat, pval= 2184960.371, 0.001
******************************
HHG mort_icu pca rf UPMCPAS 2013 6
X2_shape: (182, 1000)
runtime= 1074.2102205753326 seconds
stat, pval= 1858593.253, 0.001
******************************
HHG mort_icu pca rf UPMCPAS 2013 8
X2_shape: (167, 1000)
runtime= 995.4897954463959 seconds
stat, pval= 1433511.815, 0.001
**

runtime= 1077.824820280075 seconds
stat, pval= 1387790.158, 0.001
******************************
HHG mort_icu pca rf UPMCSHY 2013 8
X2_shape: (263, 1000)
runtime= 1537.0516121387482 seconds
stat, pval= 2355015.340, 0.001
******************************
HHG mort_icu pca rf UPMCSHY 2013 10
X2_shape: (240, 1000)
runtime= 1360.0505909919739 seconds
stat, pval= 1390922.662, 0.002
******************************
HHG mort_icu pca rf UPMCSHY 2013 12
X2_shape: (223, 1000)
runtime= 1330.1978297233582 seconds
stat, pval= 3157410.819, 0.001
******************************
HHG mort_icu pca rf UPMCSHY 2014 2
X2_shape: (187, 1000)
runtime= 1132.2854340076447 seconds
stat, pval= 1458730.056, 0.001
******************************
HHG mort_icu pca rf UPMCSHY 2014 4
X2_shape: (186, 1000)
runtime= 1089.7255334854126 seconds
stat, pval= 1864512.414, 0.001
******************************
HHG mort_icu pca rf UPMCSHY 2014 6
X2_shape: (192, 1000)
runtime= 1106.8700284957886 seconds
stat, pval= 2017090.892, 0.001
**

X2_shape: (95, 200)
runtime= 637.8449602127075 seconds
stat, pval= 2124407.885, 0.001
******************************
HHG mort_icu pca lr UPMCHZN 2011 4
X2_shape: (92, 200)
runtime= 616.612904548645 seconds
stat, pval= 1751635.852, 0.001
******************************
HHG mort_icu pca lr UPMCHZN 2011 6
X2_shape: (106, 200)
runtime= 674.026707649231 seconds
stat, pval= 3790574.190, 0.001
******************************
HHG mort_icu pca lr UPMCHZN 2011 8
X2_shape: (87, 200)
runtime= 598.8822028636932 seconds
stat, pval= 1287425.717, 0.001
******************************
HHG mort_icu pca lr UPMCHZN 2011 10
X2_shape: (75, 200)
runtime= 570.6554300785065 seconds
stat, pval= 1688186.162, 0.001
******************************
HHG mort_icu pca lr UPMCHZN 2011 12
X2_shape: (72, 200)
runtime= 551.0255875587463 seconds
stat, pval= 984373.248, 0.007
******************************
HHG mort_icu pca lr UPMCHZN 2012 2
X2_shape: (83, 200)
runtime= 595.0702331066132 seconds
stat, pval= 1624573.381, 0.001
**

X2_shape: (254, 200)
runtime= 1375.3341302871704 seconds
stat, pval= 1130561.136, 0.005
******************************
HHG mort_icu pca lr UPMCMER 2012 10
X2_shape: (233, 200)
runtime= 1309.4608426094055 seconds
stat, pval= 809553.177, 0.036
******************************
HHG mort_icu pca lr UPMCMER 2012 12
X2_shape: (166, 200)
runtime= 924.1527836322784 seconds
stat, pval= 1705503.888, 0.001
******************************
HHG mort_icu pca lr UPMCMER 2013 2
X2_shape: (168, 200)
runtime= 932.7410633563995 seconds
stat, pval= 1676638.582, 0.001
******************************
HHG mort_icu pca lr UPMCMER 2013 4
X2_shape: (175, 200)
runtime= 967.5898087024689 seconds
stat, pval= 2450861.460, 0.001
******************************
HHG mort_icu pca lr UPMCMER 2013 6
X2_shape: (150, 200)
runtime= 842.5088346004486 seconds
stat, pval= 1743719.767, 0.001
******************************
HHG mort_icu pca lr UPMCMER 2013 8
X2_shape: (178, 200)
runtime= 977.4759714603424 seconds
stat, pval= 1930899.568

X2_shape: (448, 200)
runtime= 3025.0433297157288 seconds
stat, pval= 2642115.163, 0.002
******************************
HHG mort_icu pca lr UPMCPUH 2013 4
X2_shape: (478, 200)
runtime= 3493.393321752548 seconds
stat, pval= 2429428.215, 0.001
******************************
HHG mort_icu pca lr UPMCPUH 2013 6
X2_shape: (464, 200)
runtime= 3320.9582600593567 seconds
stat, pval= 3033027.964, 0.001
******************************
HHG mort_icu pca lr UPMCPUH 2013 8
X2_shape: (447, 200)
runtime= 3084.9819481372833 seconds
stat, pval= 2550239.275, 0.001
******************************
HHG mort_icu pca lr UPMCPUH 2013 10
X2_shape: (458, 200)
runtime= 3173.0898950099945 seconds
stat, pval= 2161504.161, 0.003
******************************
HHG mort_icu pca lr UPMCPUH 2013 12
X2_shape: (398, 200)
runtime= 2532.8014907836914 seconds
stat, pval= 1478865.340, 0.006
******************************
HHG mort_icu pca lr UPMCPUH 2014 2
X2_shape: (408, 200)
runtime= 2640.123870611191 seconds
stat, pval= 3400452